In [13]:
pip install fredapi


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.3.2 -> 25.2
[notice] To update, run: C:\Users\jean-\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [14]:
import pandas as pd
import numpy as np
import os
import re
from fredapi import Fred

In [15]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)


In [16]:
pd.reset_option("all")

C:\Users\jean-\AppData\Local\Temp\ipykernel_2844\3365680546.py:1: FutureWarning: data_manager option is deprecated and will be removed in a future version. Only the BlockManager will be available.
  pd.reset_option("all")
C:\Users\jean-\AppData\Local\Temp\ipykernel_2844\3365680546.py:1: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  pd.reset_option("all")


# I- Getting the data 

For the US, we use the FRED database, available on the St Louis website, which contains a wide range of macroeconomic variables with monthly frequency. We will extract data using the FRED API and then store everything in a dataframe.

### 1) Extracting data with the API

In [22]:
api_key = '615add3bd441c0ed42dec47e952d69e2'
fred = Fred(api_key=api_key)

After many iterations, we get the following variables, which take some values between 2003-01-02 and 2025-08-01. For each of these variables, we tried to get the highest frequency of observations proposed by FRED database:
- for most financial markets data, we have daily observations
- for most macroeconomic variables, we have monthly observations
- for most fiscal variables, we have quarterly observations

Here is a list of the variables we extracted. Unfortunately, some important variables such as gold or SP500 were missing, so we will have to get these datas somewhere else.

In [18]:


variables_to_keep = [#production and revenue variables
    'RPI',  #Real personal income; monitored by FED for interest rates decisions
                   'INDPRO', #Industrial production index; leading indicator of economic health, monitored by FED 
                   #job market variables
                   'UNRATE', #unemployment rate
                   'UEMP5TO14', #unemployment for people unemployed between 5 and 14 weeks = short term unemployment
                   'UEMP27OV', #unemployment for people unemployed for 27 weeks and over = long term unemployment
                    'PAYEMS', #total non farm payroll, leading indicator of employment
                    'USGOOD',   #below is the breakdown of employment figures for various economic sectors
                    'CES1021000001',
                    'USCONS',
                    'MANEMP',
                    'DMANEMP',
                    'NDMANEMP',
                    'SRVPRD',
                    'USTPU',
                    'USWTRADE',
                    'USTRADE',
                    'USFIRE',
                    'USGOVT',
                    #consumption and housing
                    'HOUST', #housing variable, sensitive to interest rates and economic anticipations
                    'PERMIT', #same but for building permits
                    'UMCSENT', #university of michigan consumer sentiment index, important for consumption anticipations
                    #money and credit variables
                    'M1SL', #monetary base, important for interest rates and inflation anticipations
                    'M2SL', 
                    'M2REAL', #real monetary base
                    'TOTRESNS', #total reserves of banks
                    'NONBORRES', #non borrowable reserves of banks
                    'BUSLOANS', #business loans, important for growth anticipations
                    'REALLN', #real loans, related to economic activity
                    'NONREVSL', #non-revolving consumer credit, related to consumption
                    'DTCOLNVHFNM', #total nonfinancial corporate business liabilities, related to economic activity
                    'DTCTHFNM', #total household liabilities, related to consumption
                    'INVEST', #gross private domestic investment, related to economic activity
                    #price indexes
                    'CPIAUCSL', #principal measure for inflation monitored by FED
                    'CPIAUCSL', 'CPIAPPSL', 'CPITRNSL','CPIMEDSL', 'CUSR0000SAC', 'CUUR0000SAD', 'CUSR0000SAS', 'CPIULFSL', 'CUUR0000SA0L2', 'CUSR0000SA0L5', #breakdown of the index for various sectors
                    'PCEPI', #inflation target for FED
                    'DDURRG3M086SBEA', 'DNDGRG3M086SBEA', 'DSERRG3M086SBEA', #spendings for services, durable and nondurable goods
                    #fiscal variables
                    'FGEXPND', #quarterly federal government expenditures
                    'FGRECPT', #quarterly federal government receipts
                    'FGDEF',   #quarterly federal government budget deficit
                    'FGCE', # quarterly federal government spending
                    'MTSDS133FMS', # monthly federal surplus or deficit
                    'FYGFDPUN', #federal debt held by the public, quarterly 
                     'GFDEGDQ188S', #debt to gdp ratio, quarterly 
                     'A091RC1Q027SBEA', #net interest payment, quarterly 
                     'GFDEBTN', #total debt outstanding, monthly 
                     #yield variables
                     'DGS1MO', 'DGS3MO', 'DGS6MO', #yields on treasury bills with maturities < 1y
                    'DGS1', 'DGS2', 'DGS3','DGS5','DGS7', 'DGS10', 'DGS20', 'DGS30', #yields of government treasuries for maturies >=1y
                    #'GS1M','TB3MS','TB6MS', #yield on commercial paper
                    #'GS1', 'GS2', 'GS3','GS5','GS7', 'GS10', 'GS20', 'GS30', #yields of government treasuries for maturies >=1y  
                    #yields of other "safe haven"
                    'IRLTLT01DEM156N', #10y german bund yield
                    'IRLTLT01JPM156N', #10y japanese gov yield
                    'IRLTLT01GBM156N', #10y uk gilt yield
                    'IRLTLT01CAM156N', #10y canadian gov yield
                    'IRLTLT01AUM156N', #10y australian gov yield
                    'IRLTLT01FRM156N', #10y french gov yield
                    #stock markets
                    'NASDAQCOM', #nasdaq
                    #USD FX rates and US corporate bonds variables
                    'AAA', 'BAA', #yields of corporate bonds with notations AAA and BAA
                    'DEXUSEU', #usd to euro exchange rate
                    'DEXJPUS', #usd to yen exchange rate
                    'DEXUSUK', #usd to gbp exchange rate
                    'DEXCAUS', #usd to cad exchange rate
                    'DEXUSAL', #usd to aud exchange rate
                    'DEXCHUS', #usd to yuan exchange rate
                    #other financial variables measuring risk on / risk off 
                    'VIXCLS', #vix index, measure of market volatility
                    'NFCI', #national financial conditions index
                    'DCOILWTICO', #crude oil price, important for inflation anticipation
                     #interest rates variables (traditional monetary policy)
                    'FEDFUNDS', #federal funds rate, short term interest rates
                    'WRESBAL', #measure of liquidity in the banking system
                    'CURRCIR', #currency in circulation
                    'WTREGEN', #government deposits 
                    #QE and QT variables 
                    'BOGMBASE', #monetary base
                    'WSHOSHO', #total assets of FED = size of balance sheet
                    'WSHOTSL', #total treasuries held by FED
                    'WSHOBL', #total longer duration trasuries held by FED (for long end of yield curve)
                    #anticipations of inflation by markets
                    'T5YIE', #5y forward inflation expectation
                    'T10YIE', #10y forward inflation expectation

                    ]




start_date = '2003-01-02' #we don't do a start date because lots of data are missing before that 
end_date   = '2025-08-01'


In [23]:
data = {}
for code_variable in variables_to_keep:
    print(code_variable)
    try:
        series = fred.get_series(code_variable, observation_start=start_date, observation_end=end_date)
        data[code_variable] = series
    except ValueError:
        print(f"Could not retrieve data for {code_variable}")
        continue

RPI
INDPRO
UNRATE
UEMP5TO14
UEMP27OV
PAYEMS
USGOOD
CES1021000001
USCONS
MANEMP
DMANEMP
NDMANEMP
SRVPRD
USTPU
USWTRADE
USTRADE
USFIRE
USGOVT
HOUST
PERMIT
UMCSENT
M1SL
M2SL
M2REAL
TOTRESNS
NONBORRES
BUSLOANS
REALLN
NONREVSL
DTCOLNVHFNM
DTCTHFNM
INVEST
CPIAUCSL
CPIAUCSL
CPIAPPSL
CPITRNSL
CPIMEDSL
CUSR0000SAC
CUUR0000SAD
CUSR0000SAS
CPIULFSL
CUUR0000SA0L2
CUSR0000SA0L5
PCEPI
DDURRG3M086SBEA
DNDGRG3M086SBEA
DSERRG3M086SBEA
FGEXPND
FGRECPT
FGDEF
FGCE
MTSDS133FMS
FYGFDPUN
GFDEGDQ188S
A091RC1Q027SBEA
GFDEBTN
DGS1MO
DGS3MO
DGS6MO
DGS1
DGS2
DGS3
DGS5
DGS7
DGS10
DGS20
DGS30
IRLTLT01DEM156N
IRLTLT01JPM156N
IRLTLT01GBM156N
IRLTLT01CAM156N
IRLTLT01AUM156N
IRLTLT01FRM156N
NASDAQCOM
AAA
BAA
DEXUSEU
DEXJPUS
DEXUSUK
DEXCAUS
DEXUSAL
DEXCHUS
VIXCLS
NFCI
DCOILWTICO
FEDFUNDS
WRESBAL
CURRCIR
WTREGEN
BOGMBASE
WSHOSHO
WSHOTSL
WSHOBL
T5YIE
T10YIE


To account for missing data on weekly, monthly, quarterly time series, we'll use forward fill. We will also use backward fill after that to fill the first values missing in january 2003. This should not introduce any forward bias as all time series have a start date before the 8th of January 2003.

In [31]:
df = pd.concat(data, axis=1)
df.columns = data.keys()
df.to_csv('data_fred.csv',index = True)

In [32]:
df = pd.read_csv('data_fred.csv', index_col=0, parse_dates=True)
df = df.ffill()
df = df.bfill()
df

RPI    INDPRO  UNRATE  UEMP5TO14  UEMP27OV    PAYEMS  \
2003-01-01  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-02  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-03  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-06  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-07  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-08  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-09  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-10  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-13  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-14  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-15  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-16  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-17  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-20  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-21  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-22  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-23  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-24  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-27  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-28  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-29  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-30  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-01-31  12033.660   91.1369     5.8     2582.0    1760.0  130573.0   
2003-02-01  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-03  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-04  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-05  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-06  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-07  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-10  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-11  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-12  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-13  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-14  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-17  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-18  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-19  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-20  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-21  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-24  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-25  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-26  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-27  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-02-28  11991.075   91.2505     5.9     2611.0    1864.0  130441.0   
2003-03-01  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-03  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-04  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-05  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-06  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-07  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-10  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-11  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-12  12008.784   91.0006     5.9     2567.0    1798.0  130235.0   
2003-03-13  12008.784 

In [28]:
pd.set_option('display.max_rows', None)
first_valid_indices = df.apply(lambda col: col.first_valid_index())

print(first_valid_indices)

RPI               2003-01-01
INDPRO            2003-01-01
UNRATE            2003-01-01
UEMP5TO14         2003-01-01
UEMP27OV          2003-01-01
PAYEMS            2003-01-01
USGOOD            2003-01-01
CES1021000001     2003-01-01
USCONS            2003-01-01
MANEMP            2003-01-01
DMANEMP           2003-01-01
NDMANEMP          2003-01-01
SRVPRD            2003-01-01
USTPU             2003-01-01
USWTRADE          2003-01-01
USTRADE           2003-01-01
USFIRE            2003-01-01
USGOVT            2003-01-01
HOUST             2003-01-01
PERMIT            2003-01-01
UMCSENT           2003-01-01
M1SL              2003-01-01
M2SL              2003-01-01
M2REAL            2003-01-01
TOTRESNS          2003-01-01
NONBORRES         2003-01-01
BUSLOANS          2003-01-01
REALLN            2003-01-01
NONREVSL          2003-01-01
DTCOLNVHFNM       2003-01-01
DTCTHFNM          2003-01-01
INVEST            2003-01-01
CPIAUCSL          2003-01-01
CPIAPPSL          2003-01-01
CPITRNSL      